## Research Questions Focus Areas

- Note: Please endeavour to explicitly comment your codes and properly document whichever functions created so as to help other collaborators learn from your codes quicker. Remember that the project is also a learning process.

---

### Dataset Import

In [1]:
!pip install langdetect

  Created wheel for langdetect: filename=langdetect-1.0.9-py3-none-any.whl size=993242 sha256=621ed794afe4fb37034abf6a4b1326739028984a238f30c0cadd56308b75495a
  Stored in directory: c:\users\abiye\appdata\local\pip\cache\wheels\d1\c1\d9\7e068de779d863bc8f8fc9467d85e25cfe47fa5051fff1a1bb
Successfully built langdetect


In [2]:
!pip install googletrans==3.1.0a0

ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
spyder 5.1.5 requires pyqt5<5.13, which is not installed.
spyder 5.1.5 requires pyqtwebengine<5.13, which is not installed.
conda-repo-cli 1.0.4 requires pathlib, which is not installed.
anaconda-project 0.10.2 requires ruamel-yaml, which is not installed.


  Created wheel for googletrans: filename=googletrans-3.1.0a0-py3-none-any.whl size=16382 sha256=c616867f2a11ae069b8e6aaecdb02c2f01b755f5b8c012e7680d6d66db3f9d0f
  Stored in directory: c:\users\abiye\appdata\local\pip\cache\wheels\ae\e1\6c\5137bc3f35aa130deea71575e165cc4f4f0680a88f3d90a636
Successfully built googletrans
  Attempting uninstall: idna
    Found existing installation: idna 3.3
    Uninstalling idna-3.3:
      Successfully uninstalled idna-3.3
  Attempting uninstall: chardet
    Found existing installation: chardet 4.0.0
    Uninstalling chardet-4.0.0:
      Successfully uninstalled chardet-4.0.0


In [3]:
import pandas as pd
import re
from langdetect import detect
from googletrans import Translator

In [89]:
pd.set_option("display.max_colwidth", None)
pd.set_option("display.max_rows", None)

tweets = pd.read_csv("citizensvoice_dataset.csv", index_col=0)

In [90]:
tweets.head()

time_created  \
0  2022-10-25T23:44:56+00:00   
1  2022-10-25T23:37:40+00:00   
2  2022-10-25T23:31:19+00:00   
3  2022-10-25T23:03:57+00:00   
4  2022-10-27T23:59:39+00:00   

                                                                                                                                                                                                                      tweet  \
0                                                                     Tinubu Is An Emperor; Buhari, Osinbajo, Governors Begged Him To Forgive Ambode But He Refused —Dele Momodu | Sahara Reporters https://t.co/mO1zWgXQxn   
1                                                                 Dear @PeterObi please stop putting our future at risk. \nYou are the only reason I still believe in Nigeria. \nMy vote is for you https://t.co/nKhLhzrV8H   
2          Wike pointed to how the PDP presidential candidate, Alhaji Atiku Abubakar picked people from Rivers State as members of the presidential campaign council without any input from him.\n\nhttps://t.co/H2cicBJlu1   
3                                                                                                                                                                               @fkeyamo @apc_lagos https://t.co/KrKdTG8prX   
4  PDP is in total chaos in Ogun, dead in Lagos, Oyo PDP refusing to work for Atiku, the leaders in Ekiti and Ondo are refusing to mount a challenge, only in Osun does the party have a deem hope. https://t.co/w3r3dmSa0i   

        loca_tion  sentiment  discourse_area  
0         Nigeria        NaN             NaN  
1  Lagos, Nigeria        NaN             NaN  
2         Nigeria        NaN             NaN  
3   Ogun, Nigeria        NaN             NaN  
4   Ogun, Nigeria        NaN             NaN

### Dataset Wrangling

+ Using one of our Research Questions to guide the data wrangling. If we consider a simple question of "What is being said about Peter Obi?";

In [91]:
tweets.tweet = tweets.tweet.str.lower()

#### 1. Cleaning

+ Cleaning: Clean any element of the dataset that might affect our NLP algorithm.
        - Remove "/n", links and emojis.
        - Replace &amp; with and.
+ In future versions of this project, we might try to analyse some of these element, like the emojis as they could be essential for our sentimental analysis, but for now we keep it simple and focus on the execution.

In [92]:
# Unicode for emojis
emojis = re.compile("["
        u"\U0001F600-\U0001F64F"  # emoticons
        u"\U0001F300-\U0001F5FF"  # symbols & pictographs
        u"\U0001F680-\U0001F6FF"  # transport & map symbols
        u"\U0001F1E0-\U0001F1FF"  # flags (iOS)
        u"\U00002500-\U00002BEF"  # chinese char
        u"\U00002702-\U000027B0"
        u"\U00002702-\U000027B0"
        u"\U000024C2-\U0001F251"
        u"\U0001f926-\U0001f937"
        u"\U00010000-\U0010ffff"
        u"\u2640-\u2642" 
        u"\u2600-\u2B55"
        u"\u200d"
        u"\u23cf"
        u"\u23e9"
        u"\u231a"
        u"\ufe0f"  # dingbats
        u"\u3030"
                      "]+", re.UNICODE)

In [93]:
def clean_tweet(tweet):
    """
    Function to clean tweet by:
    - Changing '&' sign to and
    - Removing newlines, carriage returns, links, emojis, hashtags and puntuations

    Parameters:
        tweet (string): The tweet
    """      
            
    tweet = re.sub("\n", "", tweet) # remove newlines
    tweet = re.sub("\r", "", tweet) # remove carriage returns
    tweet = re.sub(r"http\S+", "", tweet) # removes links
    tweet = re.sub(emojis, "", tweet) # remove emojis
    tweet = re.sub(r"#(\w+)", "", tweet) # remove hashtags
    tweet = re.sub("&", "and", tweet) # changes & sign to and
    tweet = re.sub(r"[^\w\s\@]","",tweet) # removes punctuation
    tweet = tweet.strip()

    return tweet

In [94]:
tweets["clean_tweet"] = tweets.tweet.apply(clean_tweet)

In [95]:
tweets[["tweet", "clean_tweet"]].sample(30)

tweet  \
41356       @ogbonnanur @abbakila @mr_jags @thisisademuyiwa @dolusegun @officialabat he can't work for tinubu bcos he has a preferred governorship candidate running under nnpp...he wouldn't want to confuse the electorates in kano.  \n\nworking for tinubu can only be actualisable or possible if there's is a presidential rerun.   
7126                                                                                                   @adeyanjudeji if not that @govwike is fighting my next president of this country come 2023 @atiku, is still my day one man.\n\nplease my president @atiku find way to accommodate @govwike because we need his energy and vibes.   
13840                                                                                                                                    @lex_teflondon @peterobi all aspects of economy is in terrible state. i trust #peterobi is going to jugular of all the economies. nigeria shall be great again  vote wisely for better nigeria   
51344                                                                                                                                                                                                                                                         @stephengma01 nope , it's going to be a pre-recorded interview like atiku   
26823                                                                                                                                                                                                                                                                                           @1stoktobar @obijamesuk @peterobi 😂😂😂😂😂   
28652                                                                                                            @_dinomelaye daddy dino @_dinomelaye that means your candidate @atiku saw the shooting beforehand. haha baba if na young man talk like this now una go say na childish talk. as na you come talk, wetin we go call am.   
28688                                                                                                                            @chukwumauzor13 @adebayor18 @ososachris @peterobi the state that he personalizes its assets still doing well than any other state, even your obi is living in the state that he personalized the asset   
28348                                                                                                                                                                                                                                   aisha buhari: we are not sure we have met the expectations of nigerians https://t.co/afhp5kqssa   
50376                                                            @aliflabng @kelvinkage95 @tinubuoclock so pdp was a south eastern party…hmm, i just dey pity your ignorance. remember, after the war, igbos were given £25. look where they are today. dem go survive. that money wey baba give you go soon finish, your eye go clear.   
23487                                                                                                                                                                             voting for @peterobi will be response to the remembrance of #endsars .\nthe memory should guide our decision in the next general elections.\nendsars✊   
12500                                                                                                                                                                                                         @g_makuachukwu3 but the fool later returned back to pdp. so how does what he said relate? forget bitter losers in life!!!   
37389                                                                                                                                                                                                                                                                    @omoobaakintayo @princeujay how many times you don pin buhari?   
25701              

#### 2. Translate

+ Convert all tweets to lower case.
+ Translate: Here we convert all non-english tweet to English for a smooth and uniform analysis
        - If text is not in English convert to English (using google translate or any other suitable library or api).
+ This is much time saving as systems have already been develped for such translation, instead of us having to develop our NLP kit or algorithm for each language used in the Nigerian twitter space. We can simply translate with the already existing systems and then analyse with the already trained systems.
+ In future versions of this project, we could look into developing our own custom NLP algorithm and kit tailored to our own native languages.

In [97]:
translator = Translator()

In [98]:
def translate_tweet(tweet):

    """
    Function to translate non-english tweets by checking if the tweet is non-english
    and translating it using the googletrans library.
    It returns the unchanaged tweet if it is in english, a space, empty or numeric.

    Parameters:
        tweet (string): The tweet
    """ 
    if tweet.isspace() or (not tweet) or tweet.isnumeric():
        return tweet

    if detect(tweet) != "en":
        return translator.translate(tweet).text

    return tweet

In [105]:
def find_non_english(tweet):
    """
    Function that finds non-english tweets.
    
    Parameters:
        tweet (string): The tweet
    """ 
    if tweet.isspace() or (not tweet) or tweet.isnumeric():
        return False

    if detect(tweet) != "en":
        return True

    return False

In [100]:
%%time
tweets["translated_tweet"] = tweets.clean_tweet.apply(translate_tweet)

CPU times: total: 6min 8s
Wall time: 24min 55s


In [106]:
%%time
non_english = tweets.clean_tweet.apply(find_non_english)

CPU times: total: 5min 53s
Wall time: 5min 53s


In [108]:
tweets[non_english][["clean_tweet", "translated_tweet"]]

clean_tweet  \
3                                                                                                                                                                                                                                                                                                           @fkeyamo @apc_lagos   
14                                                                                                                                                                                                                                                                                         @abkgrady @atiku thank you my leader   
19                                                                                                                                                                                                                                                                                                                   @atiku sir   
20                                                                                                                                                                                                                                                                                       @docomeiza make buhari comot i go stop   
22                                                                                                                                                                                                                                                                                             @egi_nupe_ atiku is nobodys mate   
34                                                                                                                                                                                                                                                                                                                 pdp  nigeria   
38                                                                                                                                                                                                                                                                                                @anthonyehilebo @atiku simple   
42                                                                                                                                                                                                                                                                                    @bwaladaniel @peterobi @officialabat hmmm   
46                                                                                                                                                                                                                                                                 @nglabour @peterobi @yunusatanko @kennedy4aha @aburechambers   
48                                                                                                                                                                                                                                                                                                         @peterobi noisemaker   
49                                                                                                                                                                                                                                                                                                                    @peterobi   
54                                                                                                                                                                                                                                                                                                @peterobi peter obi is coming   
55                                                                                                           

#### 3. Filtering

+ Filtering: Filter for tweets directed at Peter Obi, based on the following rules:
        - Peter Obi's handle appears first in tweet.
        - Peter Obi's name (not handle) appears any where in tweet.
        - Peter Obi's handle appears in tweet but not after another handle.
+ These rule help us focus the results on tweet directed to or about Peter Obi, instead of including tweets that could simply be replies to other twitter users under Peter Obi's tweet or replies to other twitter users who posted a tweet with Peter Obi's handle in it.
+ These rules were derived from domain knowledge of the platform.

In [110]:
def filter_tweet(tweet, handle, mentions):
    """
    Function that filters tweet Filter for tweets directed at handle, based on the following rules:
    - The handle appears first in tweet.
    - The handle appears in tweet but not after another handle.
    - The person is mentioned any where in tweet based on the list of metions.

    Parameters:
        tweet (string): The tweet
        handle (string): The username of the subject to be filtered for should start with '@'
        mentions (list): A list of other ways the subject could be mentioned in the text
    """

    # Split text into tokens
    tokens = tweet.split()

    # Check for tokens that have the handle
    indices = [i for i, token in enumerate(tokens) if token == handle]

    for index in indices:

        # Checks if the handle appear first
        if index==0:
            return True

        # Checks if the another handle appears before it
        if not tokens[index-1].startswith("@"):
            return True

    # Checks if the person is mentioned anywhere in the tweet
    for mention in mentions:
        if mention in tweet:
            return True
    
    return False

In [111]:
po_tweets = tweets[tweets.translated_tweet.apply(filter_tweet, handle="@peterobi", mentions=["peter obi", " peterobi", " po "])].copy()

In [112]:
po_tweets.sample(40)

time_created  \
37893  2022-10-26T14:09:46+00:00   
28497  2022-10-20T16:13:15+00:00   
3343   2022-10-25T20:11:02+00:00   
27771  2022-10-20T16:38:56+00:00   
33357  2022-10-26T18:44:14+00:00   
6175   2022-10-25T17:29:22+00:00   
18084  2022-10-27T12:48:59+00:00   
38712  2022-10-26T13:22:20+00:00   
25872  2022-10-20T18:05:38+00:00   
31219  2022-10-26T21:28:10+00:00   
42791  2022-10-23T19:19:59+00:00   
29784  2022-10-20T15:07:10+00:00   
21     2022-10-20T23:58:04+00:00   
39741  2022-10-26T12:19:07+00:00   
23104  2022-10-20T20:05:28+00:00   
13732  2022-10-27T18:38:25+00:00   
24492  2022-10-20T19:03:19+00:00   
58630  2022-10-24T14:16:05+00:00   
54836  2022-10-24T17:42:28+00:00   
23743  2022-10-20T19:34:49+00:00   
28492  2022-10-20T16:13:26+00:00   
39322  2022-10-26T12:43:39+00:00   
50548  2022-10-24T22:23:56+00:00   
58866  2022-10-24T14:00:52+00:00   
25738  2022-10-20T18:13:21+00:00   
15921  2022-10-27T15:35:52+00:00   
7464   2022-10-25T16:07:20+00:00   
55746  2022-10-24T16:46:04+00:00   
10199  2022-10-26T23:48:56+00:00   
41912  2022-10-23T20:21:04+00:00   
38472  2022-10-26T13:35:14+00:00   
46511  2022-10-23T15:35:30+00:00   
53017  2022-10-24T19:30:39+00:00   
28578  2022-10-20T16:10:31+00:00   
25526  2022-10-20T18:22:14+00:00   
46683  2022-10-23T15:26:17+00:00   
45032  2022-10-23T17:02:44+00:00   
48173  2022-10-23T14:04:10+00:00   
29057  2022-10-20T15:47:01+00:00   
42361  2022-10-23T19:49:56+00:00   

                                                                                                                                                                                                                                                                                                                                  tweet  \
37893                           tinubu enter kano, and kano people come begin sit at home. 🤣haba! e reach jagaban turn, kano people come wise. everything working out well for peter obi. po for president.💪\n\narise tv obasanjo muslim-muslim mount kilimanjaro nancy ipob naira labour party funsho williams https://t.co/7qxlod1q1k   
28497                                                                                                                                                                                                                                                                                                                @peterobi obidient   
3343                                                                                                                   every day i wake up,  i pray for @peterobi to become the next president of nigeria..by that time hardship will be the thing of the past. no more poverty and insecurities in the country https://t.co/jcrpmrouzr   
27771                                                                                                          @peterobi is just trying to score a cheap point in politicizing a natural disaster. something @atiku and @iaokowa, the pdp vice presidential candidate has been doing that without making noise. https://t.co/ry60wxpcru   
33357                                                                                                                            @m0narch_dev @realolaudah all of bat and milano voters chose po as their worst choice. it's really about the threat to their own candidate.\nall the other nigerian chose apc as their worst candidate   
6175                                                                                                                                                                                                                                 @ikennaakaniru @fpo426 @renoomokri they might be shocked people voted pdp in 2019 cos of peter obi   
18084                                                                                                                                                                                                                             

In [47]:
len(po_tweets)

9134

### General Trends 

- This sections covers the generic trends existing amongst citizens' discussion groups.
        - What is most talked about (regardless of area or topic)

### Citizens' Sentiment

- This section covers citizens' reactions and general sentiment towards certain topic (e.g areas of developments, policies, politically significant events, public office holders' performance and so on).
        - What is the general sentiment of the citizens?
		- What is most discussed(election and governance related)?
		- What is the sentiment towards what is being discussed? 

### Complaint Areas

- This section covers the extraction of various areas of complaints and dissatisfaction amongst citizens (in different aspects of government).
        - What are the various areas of complaints as regards to governance?
		- What are the levels of sentiment towards the various area of complaints?

### Politician's Reputation

- This section covers what citizens's think about certain public office holders, their sentiment towards these individuals and their general popularity or notoriety.
        - Who is most talked about?
		- Popularity or notoreity of the most talked about.
		- Most popular, and most notorious candidates/politician.
		- How much is a certain candidate being talked about?
		- What is being said about each candidate?
		- What is the general sentiment of what is being said?